In [234]:
import geopandas as gpd
import matplotlib.pyplot as plt
import mplleaflet
from geopandas.plotting import plot_polygon_collection
import tilemapbase
tilemapbase.init(create=True)
import folium
from folium.features import DivIcon
import pandas as pd
import plotly.express as px
import numpy as np
import matplotlib.colors as mcolors
import seaborn as sns

Tokyo_grid = pd.read_csv('/home/is/shuntaro-o/dev/compare_population_and_tweet_number/data/grid_data/SDDSWS5339/Tokyo_grid.csv')
Kyoto_grid = pd.read_csv('/home/is/shuntaro-o/dev/compare_population_and_tweet_number/data/grid_data/QDDSWQ5235/Kyoto_grid.csv')


In [235]:
# Seabornのカラーパレットを取得
palette = sns.color_palette("Reds", 24)  # 例として "deep" パレットを使用

# カラーパレットの各色をhex値に変換
hex_values = [mcolors.to_hex(color) for color in palette]

# 結果の表示
print(hex_values)

['#ffeee7', '#fee8dd', '#fee1d4', '#fdd7c6', '#fdcab5', '#fcbea5', '#fcb296', '#fca588', '#fc9777', '#fc8a6a', '#fb7d5d', '#fb7151', '#f96245', '#f5533b', '#f14432', '#eb372a', '#de2b25', '#d32020', '#c8171c', '#bc141a', '#af1117', '#a10e15', '#8e0912', '#7a0510']


In [246]:
palette

[(0.9987697039600154, 0.9349480968858132, 0.9042675893886967),
 (0.9975394079200308, 0.9091118800461361, 0.867358708189158),
 (0.9963091118800461, 0.883275663206459, 0.8304498269896193),
 (0.994079200307574, 0.8414455978469819, 0.7745482506728181),
 (0.9913725490196079, 0.7913725490196079, 0.7082352941176471),
 (0.9889119569396386, 0.7458515955401769, 0.6479507881584006),
 (0.9882352941176471, 0.6967627835447904, 0.5894502114571318),
 (0.9882352941176471, 0.6463206459054209, 0.5316262975778547),
 (0.9882352941176471, 0.5908342945021146, 0.4680199923106498),
 (0.9874509803921568, 0.5411764705882353, 0.41568627450980394),
 (0.9862206843521722, 0.49196462898885046, 0.3664744329104191),
 (0.9849903883121875, 0.44275278738946566, 0.3172625913110343),
 (0.9761937716262975, 0.3838831218762015, 0.2698961937716263),
 (0.9614302191464821, 0.3260592079969243, 0.23298731257208766),
 (0.9466666666666667, 0.26823529411764707, 0.19607843137254902),
 (0.921199538638985, 0.21576316801230297, 0.16585928489042676),
 (0.8724798154555939, 0.16839677047289503, 0.1455594002306805),
 (0.8281891580161476, 0.1253364090734333, 0.12710495963091117),
 (0.7832218377547097, 0.0910726643598616, 0.11101883890811226),
 (0.7364705882352941, 0.08, 0.10117647058823528),
 (0.685044213763937, 0.06782006920415225, 0.09034986543637061),
 (0.6327566320645905, 0.05536332179930796, 0.08050749711649365),
 (0.556478277585544, 0.03690888119953864, 0.07066512879661667),
 (0.4801999231064975, 0.01845444059976932, 0.06082276047673971)]

In [236]:
Tokyo_residents_max = Tokyo_grid['residents'].max()
Tokyo_residents_min = Tokyo_grid['residents'].min()
Kyoto_residents_max = Kyoto_grid['residents'].max()
Kyoto_residents_min = Kyoto_grid['residents'].min()

if (Tokyo_residents_max > Kyoto_residents_max):
    residents_max = Tokyo_residents_max
else:
    residents_max = Kyoto_residents_max


if (Tokyo_residents_min < Kyoto_residents_min):
    residents_min = Tokyo_residents_min
else:
    residents_min = Kyoto_residents_min

In [237]:
interval_values = np.linspace(residents_min, residents_max, 24)
interval_values
# interval_values = np.linspace(Tokyo_residents_min, Tokyo_residents_max, 6)
# interval_values

array([1.00000000e+00, 1.42295652e+03, 2.84491304e+03, 4.26686957e+03,
       5.68882609e+03, 7.11078261e+03, 8.53273913e+03, 9.95469565e+03,
       1.13766522e+04, 1.27986087e+04, 1.42205652e+04, 1.56425217e+04,
       1.70644783e+04, 1.84864348e+04, 1.99083913e+04, 2.13303478e+04,
       2.27523043e+04, 2.41742609e+04, 2.55962174e+04, 2.70181739e+04,
       2.84401304e+04, 2.98620870e+04, 3.12840435e+04, 3.27060000e+04])

In [238]:
def find_interval(number, interval_values):
    """
    入力された数字がinterval_valuesのどの範囲に属するかを判定する関数

    Parameters:
    - number: 判定する数字
    - interval_values: 区間の配列

    Returns:
    - interval: 数字が属する区間（例: (0, 20)）
    """
    for i in range(len(interval_values) - 1):
        if interval_values[i] <= number <= interval_values[i + 1]:
            return i
    # 数字がどの範囲にも属さない場合
    return None

In [239]:
Tokyo_grid['color_num'] = Tokyo_grid['residents'].apply(lambda x: find_interval(x, interval_values))
Kyoto_grid['color_num'] = Kyoto_grid['residents'].apply(lambda x: find_interval(x, interval_values))

In [240]:
Tokyo_map = folium.Map(location=[35.690921, 139.700258], zoom_start=15)
folium.TileLayer('cartodbpositron').add_to(Tokyo_map)
meth_list=[53394611, 52353680, 52354610, 52354642, 52354513, 52354548, 52353692, 52354519, 52353579]
colors = ['#1f77b4', '#ff7f0e', '#2ca02c', '#d62728', '#9467bd', '#8c564b', '#e377c2', '#7f7f7f', '#bcbd22']
place_list = ['Tokyo Staion', 'Kyoto Station', 'Nakagyo ward', 'Kyoto university', 'Arashiyama', 'Kinkaku-ji temple', 'Kiyomizu-dera temple', 'Nijo-jo castle', 'To-ji temple']
place_snwe = [[35.675, 139.7625, 35.683333333333, 139.775],
              [34.983333333333, 135.75, 34.99166666666, 135.7625],
              [35.008333333333, 135.75, 35.016666666667, 135.7625],
              [35.033333333333, 135.775, 35.041666666667, 135.7875],
              [35.008333333333, 135.6625, 35.016666666667, 135.675],
              [35.033333333333, 135.725, 35.041666666667, 135.7375],
              [34.991666666667, 135.775, 35, 135.7875],
              [35.008333333333, 135.7375, 35.01666666666, 135.75],
              [34.975, 135.7375, 34.983333333333, 135.75]]

for idx, snwe in enumerate(place_snwe):
    s = snwe[0]
    w = snwe[1]
    n = snwe[2]
    e = snwe[3]



    folium.Polygon(
        locations=[[s,w], [s,e], [n,e], [n,w]], # 多角形の頂点
        color="red", # 線の色
        weight=5, # 線の太さ
        fill=False, # 塗りつぶす
        fill_opacity=0.5, # 透明度（1=不透明）
    ).add_to(Tokyo_map)



    folium.Marker(location=[(s+n)/2 + 0.004, (w+e)/2 - 0.005], icon=DivIcon(
        icon_size=(80, 25),
        icon_anchor=(0, 0),
        html='<div style="text-align: left; font-size: 15pt; color : black width: 100px; height: 25px, font-weight: 1000">'+ place_list[idx] +'</div>')
    ).add_to(Tokyo_map)


In [241]:
Kyoto_map = folium.Map(location=[34.983333333333, 135.75], zoom_start=15)
folium.TileLayer('cartodbpositron').add_to(Kyoto_map)
meth_list=[53394611, 52353680, 52354610, 52354642, 52354513, 52354548, 52353692, 52354519, 52353579]
colors = ['#1f77b4', '#ff7f0e', '#2ca02c', '#d62728', '#9467bd', '#8c564b', '#e377c2', '#7f7f7f', '#bcbd22']
place_list = ['Tokyo Staion', 'Kyoto Station', 'Nakagyo ward', 'Kyoto university', 'Arashiyama', 'Kinkaku-ji temple', 'Kiyomizu-dera temple', 'Nijo-jo castle', 'To-ji temple']
place_snwe = [[35.675, 139.7625, 35.683333333333, 139.775],
              [34.983333333333, 135.75, 34.99166666666, 135.7625],
              [35.008333333333, 135.75, 35.016666666667, 135.7625],
              [35.033333333333, 135.775, 35.041666666667, 135.7875],
              [35.008333333333, 135.6625, 35.016666666667, 135.675],
              [35.033333333333, 135.725, 35.041666666667, 135.7375],
              [34.991666666667, 135.775, 35, 135.7875],
              [35.008333333333, 135.7375, 35.01666666666, 135.75],
              [34.975, 135.7375, 34.983333333333, 135.75]]

for idx, snwe in enumerate(place_snwe):
    s = snwe[0]
    w = snwe[1]
    n = snwe[2]
    e = snwe[3]



    folium.Polygon(
        locations=[[s,w], [s,e], [n,e], [n,w]], # 多角形の頂点
        color="red", # 線の色
        weight=5, # 線の太さ
        fill=False, # 塗りつぶす
        fill_opacity=0.5, # 透明度（1=不透明）
    ).add_to(Kyoto_map)



    folium.Marker(location=[(s+n)/2 + 0.004, (w+e)/2 - 0.005], icon=DivIcon(
        icon_size=(80, 25),
        icon_anchor=(0, 0),
        html='<div style="text-align: left; font-size: 15pt; color : black width: 100px; height: 25px, font-weight: 1000">'+ place_list[idx] +'</div>')
    ).add_to(Kyoto_map)

In [242]:
for i in range(len(Tokyo_grid)):
    s = Tokyo_grid.miny[i]
    w = Tokyo_grid.minx[i]
    n = Tokyo_grid.maxy[i]
    e = Tokyo_grid.maxx[i]


    if pd.isna(Tokyo_grid['color_num'][i]):  # もしくは df['num'].isna().iloc[i] でも可
        folium.Polygon(
            color = 'gray',
            locations=[[s,w], [s,e], [n,e], [n,w]], # 多角形の頂点
            weight=1, # 線の太さ
            fill=False, # 塗りつぶす
            fill_opacity=0.5, # 透明度（1=不透明）
        ).add_to(Tokyo_map)
    else:
        folium.Polygon(
            color=hex_values[int(Tokyo_grid['color_num'][i])],
            locations=[[s,w], [s,e], [n,e], [n,w]], # 多角形の頂点
            weight=1, # 線の太さ
            fill=True, # 塗りつぶす
            fill_opacity=0.5, # 透明度（1=不透明）
        ).add_to(Tokyo_map)



In [243]:
for i in range(len(Kyoto_grid)):
    s = Kyoto_grid.miny[i]
    w = Kyoto_grid.minx[i]
    n = Kyoto_grid.maxy[i]
    e = Kyoto_grid.maxx[i]


    if pd.isna(Kyoto_grid['color_num'][i]):  # もしくは df['num'].isna().iloc[i] でも可
        folium.Polygon(
            color = 'gray',
            locations=[[s,w], [s,e], [n,e], [n,w]], # 多角形の頂点
            weight=1, # 線の太さ
            fill=False, # 塗りつぶす
            fill_opacity=0.5, # 透明度（1=不透明）
        ).add_to(Kyoto_map)
    else:
        folium.Polygon(
            color=hex_values[int(Kyoto_grid['color_num'][i])],
            locations=[[s,w], [s,e], [n,e], [n,w]], # 多角形の頂点
            weight=1, # 線の太さ
            fill=True, # 塗りつぶす
            fill_opacity=0.5, # 透明度（1=不透明）
        ).add_to(Kyoto_map)

In [244]:
Tokyo_map

In [245]:
Kyoto_map